In [1]:
from skewPy import SkewT
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import glob
from datetime import datetime
from __future__ import division
import scipy as sp  # SciPy (signal and image processing library)
import matplotlib as mpl         # Matplotlib (2D/3D plotting library)
from pylab import *              # Matplotlib's pylab interface
from mpl_toolkits.basemap import Basemap
import glob


# Interpolates a single variable data_in from A SINGLE .TXT FILE onto goal_hghts
def interp_all(data_in, goal_hghts, data_str):
    data_out = np.empty([len(goal_hghts), data_in[data_str].shape[1]])
    for i in range(data_in[data_str].shape[1]):
        hght_mask = np.where(data_in['hght'][:,i].mask == False)
        data_mask = np.where(data_in[data_str][:,i].mask == False)
        data_out[:,i] = np.interp(goal_hghts, data_in['hght'][:,i][hght_mask], data_in[data_str][:,i][hght_mask])
        data_out[np.where(data_out == -999)] = np.nan
    return(data_out)

# Interpolates a data_set from full monthly data formed from many files 
def interp_all_monthly(data_set_in, goal_hghts, data_str):
    data_out = np.empty([len(goal_hghts), ntimes])
    idx_start = 0
    for i in range(len(data_set_in)):
        idx_end = idx_start + data_set_in[i]['hght'].shape[1]
        #print(data_out[:, idx_start:idx_end].shape)
        #print('goal hghts', goal_hghts)
        for j in range(idx_end - idx_start):
            hght_mask = np.where(data_set_in[i]['hght'][:,j].mask == False)
            data_mask = np.where(data_set_in[i][data_str][:,j].mask == False)
            #print('actual hghts', data_set_in[i]['hght'][:,j][hght_mask])
            #print('actual hghts shape', data_set_in[i]['hght'][:,j][hght_mask].shape)
            #print('hght_mask shape ', hght_mask[0].shape)
            #print('data_mask shape ', data_mask[0].shape)
            data_out[:, idx_start+j] = np.interp(goal_hghts, \
                                       data_set_in[i]['hght'][:,j][hght_mask], \
                                       data_set_in[i][data_str][:,j][hght_mask], left=np.nan, right=np.nan)
            #print(data_out[0, idx_start+j])
            data_out[np.where(data_out == -999)] = np.nan
        idx_start = idx_end
    return(data_out)

# Function which takes a dictionary data_in and interpolate a key data_str onto heights
# goal_hghts. Might update to have automatically cycle through dictionary keys rather than
# take data_str, but not too many variables of interest to read
def interp_all_thompson(data_in, goal_hghts, data_str):
    data_out = np.empty([len(goal_hghts), len(data_in)])
    for i in range(len(data_in)):
        #print(data_in[i]['hght'])
        #print(data_in[i][data_str])
        data_out[:,i] = np.interp(goal_hghts, data_in[i]['hght'], data_in[i][data_str])
        #print(data_in[i]['hght'].max())
        #print(goal_hghts>data_in[i]['hght'].max())
        data_out[np.where(goal_hghts>data_in[i]['hght'].max()), i] = np.nan
    return(data_out)


In [2]:
# Plots the most recent sounding from each site
plt.close('all')

S1 = SkewT.Sounding(filename='/Volumes/cruiseshare/Soundings/Palau/91408_KororPalau/201808.txt', fmt='PALAU', date_to_read = -1, init_plot = 0)
S1.make_skewt_axes()
S1.add_profile(color='r', bloc=.6, bcol='r')
S1.readfile('/Volumes/cruiseshare/Soundings/Yap/201808.txt')
S1.add_profile(color='b', bloc=.8, bcol='b')

read_folder = '/Volumes/cruiseshare/Soundings/Thompson/edt/'
file_list = sorted(glob.glob(read_folder + '*'))
S1.readfile(file_list[-1], fmt='PISTON_EDT')
S1.add_profile(color='k', bloc=1, bcol='k', fmt='PISTON_EDT')



p_lcl =  948.739668034
lcl_height =  610.0


In [3]:
####################################
# Processes Palau for August 2018 #
####################################

pal_lon = 134.48
pal_lat = 7.34

file_list = ('/Volumes/cruiseshare/Soundings/Palau/91408_KororPalau/201808.txt', \
                 '/Volumes/cruiseshare/Soundings/Palau/91408_KororPalau/201809.txt')

ntimes = 0 #number of days
for file_name in file_list:
    S1 = SkewT.Sounding(file_name, fmt='PALAU', date_to_read = 0, init_plot = 0)
    ntimes = ntimes + S1.data['temp'].shape[1]
#print(ntimes)

# For reading in the data_str from the dictionary
def read_all(file_list):
    data_out = list()
    for file_name in file_list:
        S1 = SkewT.Sounding(data={}, fmt='PALAU', date_to_read = 0, init_plot=0)
        S1.readfile(file_name)
        data_out.append(S1.data)
    return(data_out)

def read_dates(file_list):
    data_out = np.empty(ntimes, dtype=datetime.datetime)
    idx_start = 0
    for file_name in file_list:
        S1 = SkewT.Sounding(file_name, fmt='PALAU', date_to_read = 0, init_plot=0)
        idx_end = idx_start + np.asarray(S1.sounding_date).shape[0]
        data_out[idx_start:idx_end] = np.asarray(S1.sounding_date)
        idx_start = idx_end

    return(data_out)
#S1.fig.legend()

palau_list = read_all(file_list)
palau_dates = read_dates(file_list)
# Reads Palau for August

#temp = np.empty(palau['temp'].shape)
z = np.linspace(0, 17000, 300)
#for i in range(len(z)palau['hght'].shape[1]):
#    temp[:,i] = np.interp(z, palau['hght'][:,i], palau['temp'][:,i])
    #dwpt = interp_all(palau, z, 'dwpt')
    #pres = interp_all(palau, z, 'pres')

pal_temp = interp_all_monthly(palau_list, z, 'temp')
pal_dwpt = interp_all_monthly(palau_list, z, 'dwpt')
pal_sknt = interp_all_monthly(palau_list, z,'sknt')
pal_drct = interp_all_monthly(palau_list, z,'drct')
#pal_dwpt[np.where((pal_dwpt > 50.) | (pal_dwpt < -100))] = np.nan


pal_relh = SkewT.RH(pal_temp, pal_dwpt)
pal_u = pal_sknt*np.cos(np.radians(270-pal_drct))
pal_v = pal_sknt*np.sin(np.radians(270-pal_drct))

# Some data management




In [4]:
####################################
# Processes Yap for August 2018 #
####################################
yap_lat = 9.50
yap_lon = 138.08

file_list = ('/Volumes/cruiseshare/Soundings/Yap/201808.txt', '/Volumes/cruiseshare/Soundings/Yap/201809.txt')

ntimes = 0 #number of days
for file_name in file_list:
    S1 = SkewT.Sounding(file_name, fmt='PALAU', date_to_read = 0, init_plot = 0)
    ntimes = ntimes + S1.data['temp'].shape[1]
#print(ntimes)

#S1.fig.legend()

yap_list = read_all(file_list)
yap_dates = read_dates(file_list)

yap_temp = interp_all_monthly(yap_list, z, 'temp')
yap_dwpt = interp_all_monthly(yap_list, z, 'dwpt')
yap_sknt = interp_all_monthly(yap_list, z, 'sknt')
yap_drct = interp_all_monthly(yap_list, z, 'drct')

# Some data management
yap_dwpt[np.where((yap_dwpt > 50.) | (yap_dwpt < -100))] = np.nan

yap_relh = SkewT.RH(yap_temp, yap_dwpt)
yap_u = yap_sknt*np.cos(np.radians(270-yap_drct))
yap_v = yap_sknt*np.sin(np.radians(270-yap_drct))

############


/Users/zanemartin/anaconda/lib/python3.6/site-packages/ipykernel/__main__.py:26: RuntimeWarning: invalid value encountered in greater
/Users/zanemartin/anaconda/lib/python3.6/site-packages/ipykernel/__main__.py:26: RuntimeWarning: invalid value encountered in less


In [5]:
####################################
# Processes Thompson for August 2018 #
####################################

# Main folder where the reading is done; creates list of all current soundings
read_folder = '/Volumes/cruiseshare/Soundings/Thompson/edt/'
file_list = sorted(glob.glob(read_folder + '*'))
#print('List of soundings: ', file_list)
#print('Most current sounding: ', file_list[-1])

# Read the most recent one
thompson = SkewT.Sounding(data={}, fmt='PISTON_EDT')
#thompson.make_skewt_axes()
thompson_data = ()
thompson_date_list = ()

for file_name,idx in zip(file_list, np.arange(len(file_list))):
    thompson.readfile(file_name)
    #S1.add_profile(color=clrs[-idx], bloc=.6 + .2*idx, bcol=clrs[-idx])
    thompson_data = np.append(thompson_data, thompson.data)
    thompson_date_list = np.append(thompson_date_list, thompson.sounding_date)

# Sets up goal heights up to 20km and interpolate tempa nd dewpt
#pres = np.linspace(100, 1000, 1000)
#temp = interp_all('temp', pres[::-1], data_set)
#dwpt = interp_all('dwpt', pres[::-1], data_set)
#pres = interp_all('pres', pres[::-1], data_set)

tom_temp = interp_all_thompson(thompson_data, z, 'temp')
tom_dwpt = interp_all_thompson(thompson_data, z, 'dwpt')
tom_pres = interp_all_thompson(thompson_data, z, 'pres')


# Calculates zonal and meridional wind from the speed and direction
tom_u = np.empty([len(z), len(thompson_data)])
tom_v = np.empty(tom_u.shape)

for i in range(len(thompson_data)):
    tom_utemp = thompson_data[i]['sknt']*np.cos(np.radians(270-thompson_data[i]['drct']))
    tom_vtemp = thompson_data[i]['sknt']*np.sin(np.radians(270-thompson_data[i]['drct']))
    tom_utemp = np.interp(z, thompson_data[i]['hght'], tom_utemp, left=np.nan, right=np.nan)
    tom_vtemp = np.interp(z, thompson_data[i]['hght'], tom_vtemp, left=np.nan, right=np.nan)
    tom_utemp[np.where(z>thompson_data[i]['hght'].max())] = np.nan
    tom_vtemp[np.where(z>thompson_data[i]['hght'].max())] = np.nan
    tom_u[:,i] = tom_utemp
    tom_v[:,i] = tom_vtemp
#print(u)

# Calculates relative humidity; might also read in and compare if in sounding
tom_relh = SkewT.RH(tom_temp, tom_dwpt)


# Calculates lat and lon, from Kyle Chudler code
files = sorted(glob.glob('/Volumes/cruiseshare/Soundings/Thompson/edt/e*'))

lat = []
lon = []
for f in files:
    data = loadtxt(f,skiprows = 30)
    lat.append(data[:,9])
    lon.append(data[:,10])

start_lon = [l[0] for l in lon]    
start_lat = [l[0] for l in lat]



In [6]:
start_date = datetime.datetime(2018, 8, 21, 0, 0)
end_date = datetime.datetime(2018, 9, 2, 0, 0)

fig = plt.figure()
ax1 = fig.add_subplot(3,1,1)
ax2 = fig.add_subplot(3,1,2)
ax3 = fig.add_subplot(3,1,3)

cf = ax1.contourf(palau_dates[79:], z, pal_u[:, 79:], np.arange(-60, 60), cmap='RdBu_r', extend='both')
ax1.set_title('Palau Zonal wind (knots)')
ax1.set_xlim([start_date, end_date])
plt.colorbar(cf, ax=ax1)

cf = ax2.contourf(yap_dates[40:], z, yap_u[:, 40:], np.arange(-60, 60), cmap='RdBu_r', extend='both')
ax2.set_title('Yap Zonal wind (knots)')
ax2.set_xlim([start_date, end_date])
plt.colorbar(cf, ax=ax2)

cf = ax3.contourf(thompson_date_list, z, tom_u, np.arange(-60, 60), cmap='RdBu_r', extend='both')
ax3.set_title('Thompson Zonal wind (knots)')
ax3.set_xlim([start_date, end_date])
plt.colorbar(cf, ax=ax3)

fig.tight_layout()
plt.show()


In [7]:
fig = plt.figure()
ax1 = fig.add_subplot(3,1,1)
ax2 = fig.add_subplot(3,1,2)
ax3 = fig.add_subplot(3,1,3)

cf = ax1.contourf(palau_dates[79:], z, pal_v[:,79:], np.arange(-30, 30), cmap='RdBu_r', extend='both')
ax1.set_title('Palau Meridional wind (knots)')
ax1.set_xlim([start_date, end_date])
plt.colorbar(cf, ax=ax1)

cf = ax2.contourf(yap_dates[40:], z, yap_v[:,40:], np.arange(-30, 30), cmap='RdBu_r', extend='both')
ax2.set_title('Yap Meridional wind (knots)')
ax2.set_xlim([start_date, end_date])
plt.colorbar(cf, ax=ax2)

cf = ax3.contourf(thompson_date_list, z, tom_v, np.arange(-30, 30), cmap='RdBu_r', extend='both')
ax3.set_title('Thompson Meridional wind (knots)')
ax3.set_xlim([start_date, end_date])
plt.colorbar(cf, ax=ax3)

fig.tight_layout()
plt.show()



In [8]:
def make_anom(data_in):
    data_out = np.empty(data_in.shape)
    for i in range(data_in.shape[1]):
        data_out[:,i] = data_in[:,i] - np.nanmean(data_in, 1)
    return(data_out)
                        
pal_relha = make_anom(pal_relh)
yap_relha = make_anom(yap_relh)
tom_relha = make_anom(tom_relh)

if 1 ==1:
    fig = plt.figure()
    ax1 = fig.add_subplot(3,1,1)
    ax2 = fig.add_subplot(3,1,2)
    ax3 = fig.add_subplot(3,1,3)

    cf = ax1.contourf(palau_dates[79:], z, pal_relha[:,79:], cmap='RdBu_r', extend='both')
    ax1.set_title('Palau Relative Humidity Anomaly (%)')
    ax1.set_xlim([start_date, end_date])
    plt.colorbar(cf, ax=ax1)

    cf = ax2.contourf(yap_dates[40:], z, yap_relha[:,40:], cmap='RdBu_r', extend='both')
    ax2.set_title('Yap Relative Humidity Anomaly (%)')
    ax2.set_xlim([start_date, end_date])
    plt.colorbar(cf, ax=ax2)

    cf = ax3.contourf(thompson_date_list, z, tom_relha, cmap='RdBu_r', extend='both')
    ax3.set_title('Thompson Relative Humidity Anomaly (%)')
    ax3.set_xlim([start_date, end_date])
    plt.colorbar(cf, ax=ax3)

    fig.tight_layout()
    plt.show()



/Users/zanemartin/anaconda/lib/python3.6/site-packages/ipykernel/__main__.py:4: RuntimeWarning: Mean of empty slice


In [9]:
pal_tempa = make_anom(pal_temp[:,79:])
yap_tempa = make_anom(yap_temp[:,40:])
tom_tempa = make_anom(tom_temp)

if 1 ==1:
    fig = plt.figure()
    ax1 = fig.add_subplot(3,1,1)
    ax2 = fig.add_subplot(3,1,2)
    ax3 = fig.add_subplot(3,1,3)

    cf = ax1.contourf(palau_dates[79:], z, pal_tempa, np.arange(-5, 5, .5),\
                      cmap='RdBu_r', extend='both')
    ax1.set_title('Palau Temperature Anomaly (C)')
    ax1.set_xlim([start_date, end_date])
    plt.colorbar(cf, ax=ax1)

    cf = ax2.contourf(yap_dates[40:], z, yap_tempa, np.arange(-5, 5, .5),\
                    cmap='RdBu_r', extend='both')
    ax2.set_title('Yap Temperature Anomaly (C)')
    ax2.set_xlim([start_date, end_date])
    plt.colorbar(cf, ax=ax2)

    cf = ax3.contourf(thompson_date_list, z, tom_tempa, np.arange(-5, 5, .5),\
                      cmap='RdBu_r', extend='both')
    ax3.set_title('Thompson Temperature Anomaly (C)')
    ax3.set_xlim([start_date, end_date])
    plt.colorbar(cf, ax=ax3)

    fig.tight_layout()
    plt.show()


/Users/zanemartin/anaconda/lib/python3.6/site-packages/ipykernel/__main__.py:4: RuntimeWarning: Mean of empty slice


In [10]:
tom_ordd = np.asarray([thompson_date_list[i].timestamp() for i in range(len(thompson_date_list))])
pal_ordd = np.asarray([palau_dates[i].timestamp() for i in range(len(palau_dates))])
yap_ordd = np.asarray([yap_dates[i].timestamp() for i in range(len(yap_dates))])

In [11]:
tom_u.shape

(300, 105)

In [12]:
tom_u_int = np.empty([len(z), len(pal_ordd[79::])])
yap_u_int = np.empty([len(z), len(pal_ordd[79::])])
pal_u_int = pal_u[:, 79::]

tom_v_int = np.empty(tom_u_int.shape)
yap_v_int = np.empty(yap_u_int.shape)
pal_v_int = pal_v[:, 79::]

for i in range(tom_u.shape[0]):
    tom_u_int[i,:] = np.interp(pal_ordd[79::], tom_ordd, tom_u[i,:])
    tom_v_int[i,:] = np.interp(pal_ordd[79::], tom_ordd, tom_v[i,:])
    tom_lon_int = np.interp(pal_ordd[79::], tom_ordd, start_lon)
    tom_lat_int = np.interp(pal_ordd[79::], tom_ordd, start_lat)

for i in range(yap_u.shape[0]):
    yap_u_int[i,:] = np.interp(pal_ordd[79::], yap_ordd[40:], yap_u[i,40:])
    yap_v_int[i,:] = np.interp(pal_ordd[79::], yap_ordd[40:], yap_v[i,40:])

In [13]:
# Calculates del_u/del_x

# Radius of the earth (m)
R = 6.371e6

# Distances to Yap and Thompson relative to Palau (m)
yap_x = (yap_lon - pal_lon)/180*np.pi*R*np.cos((pal_lat + yap_lat)/2*np.pi/180)*np.ones(yap_u_int.shape)
tom_x = (np.asarray(tom_lon_int) - pal_lon)/180*np.pi*R*np.cos((np.asarray(tom_lon_int) \
                                                              + yap_lat)/2*np.pi/180)*np.ones(yap_u_int.shape)

yap_y = (yap_lat - pal_lat)/180*np.pi*R*np.ones(yap_u_int.shape)
tom_y = (np.asarray(tom_lat_int) - pal_lat)/180*np.pi*R*np.ones(yap_u_int.shape)

# Vectors from Palau to Thompson and Palau to Yap, converts winds to m/s
P_u = np.asarray([np.zeros(yap_u_int.shape), np.zeros(yap_u_int.shape), np.zeros(yap_u_int.shape)])
Y_u = np.asarray([(yap_u_int - pal_u_int)/1.94384, yap_x, yap_y])
T_u = np.asarray([(tom_u_int - pal_u_int)/1.94384, tom_x, tom_y])

P_v = np.asarray([np.zeros(yap_u_int.shape), np.zeros(yap_u_int.shape), np.zeros(yap_u_int.shape)])
Y_v = np.asarray([(yap_v_int - pal_v_int)/1.94384, yap_x, yap_y])
T_v = np.asarray([(tom_v_int - pal_v_int)/1.94384, tom_x, tom_y])

In [14]:
pal_u_int - yap_u_int

array([[         nan,          nan,          nan, ...,          nan,
                 nan,          nan],
       [ -0.62310596,  -4.82159068,  -6.04347711, ...,   4.65006477,
         -3.02727814,   0.43155542],
       [ -3.15901763,  -7.03787481,  -8.35912756, ...,   2.84898282,
         -3.88330235,  -1.65841184],
       ..., 
       [ 21.02789669,  11.97253807,          nan, ...,  -3.00034031,
         10.69141113,  13.64262836],
       [ 19.6335045 ,  12.10805807,          nan, ...,  -4.18844906,
          9.39529381,  12.52077119],
       [ 18.29688313,  12.17167344,          nan, ...,  -5.43762667,
          8.15381238,  11.40996438]])

In [24]:
du_dx = np.empty(tom_u_int.shape)
du_dy = np.empty(du_dx.shape)

dv_dx = np.empty(du_dx.shape)
dv_dy = np.empty(du_dx.shape)

for i in range(du_dx.shape[0]):
    for j in range(du_dx.shape[1]):
        du_dx[i,j] = - np.cross(Y_u[:,i,j], T_u[:,i,j])[1] / \
        np.cross(Y_u[:,i,j], T_u[:,i,j])[0]

        du_dy[i,j] = - np.cross(Y_u[:,i,j] - P_u[:,i,j], T_u[:,i,j] - P_u[:,i,j])[2] / \
        np.cross(Y_u[:,i,j] - P_u[:,i,j], T_u[:,i,j] - P_u[:,i,j])[0]
 
        dv_dx[i,j] =  - np.cross(Y_v[:,i,j], T_v[:,i,j])[1] / \
        np.cross(Y_v[:,i,j], T_v[:,i,j] )[0] 
        
        dv_dy[i,j] =  - np.cross(Y_v[:,i,j] - P_v[:,i,j], T_v[:,i,j] - P_v[:,i,j])[2] / \
        np.cross(Y_v[:,i,j] - P_v[:,i,j], T_v[:,i,j] - P_v[:,i,j])[0] 

        


In [25]:
# Calculates pressure velocity
p = np.nanmean(tom_pres, 1) # mean pressure

div = du_dx + dv_dy # divergence
vort = dv_dx - du_dy # vorticity


w = np.zeros(div.shape)
for i in range(w.shape[1]):
    for j in np.arange(w.shape[0] - 2):
        #print('j ', j)
        # w goes to zero at bottom boundary
        if j == 0:
            w[j+1,i] = -np.sum((div[1:2, i] + div[2:3, i]))
        else:
            #print(div[1:j+2, i])
            #print(div[2:j+3, i])
            #print((div[1:j+2, i] + div[2:j+3, i])/2*np.diff(p[1:j+3]))
            #print(((div[1:j+2, i] + div[2:j+3, i])/2*np.diff(p[1:j+2])).shape)
            w[j,i] = -np.sum((div[1:j+2, i] + div[2:j+3, i])/2*np.diff(p[1:j+3]))
        
##du_dx = np.cross(Y_u.T - P_u.T, T_u.T - P_u.T)[:,:,1]/np.cross(Y_u.T - P_u.T, T_u.T - P_u.T)[:,:,0]
##du_dy = np.cross(Y_u.T - P_u.T, T_u.T - P_u.T)[:,:,2]/np.cross(Y_u.T - P_u.T, T_u.T - P_u.T)[:,:,0]

#dv_dx = np.cross(Y_v.T - P_v.T, T_v.T - P_v.T)[:,:,1]/np.cross(Y_v.T - P_v.T, T_v.T - P_v.T)[:,:,0]
#dv_dy = np.cross(Y_v.T - P_v.T, T_v.T - P_v.T)[:,:,2]/np.cross(Y_v.T - P_v.T, T_v.T - P_v.T)[:,:,0]

In [27]:
plt.close('all')

plt.figure()
plt.subplot(3,1,1)
plt.contourf(palau_dates[79::], p, du_dx + dv_dy, np.linspace(-5e-5, 5e-5, 20), \
             cmap='RdBu_r', extend='both')
plt.gca().invert_yaxis()
plt.colorbar(format='%.0e')
plt.title('Divergence')

plt.subplot(3,1,2)
plt.contourf(palau_dates[79::], p, dv_dx - du_dy, np.linspace(-5e-5, 5e-5, 20), \
             cmap='RdBu_r', extend='both')
plt.gca().invert_yaxis()
plt.colorbar(format='%.0e')
plt.title('Vorticity')
plt.tight_layout()

plt.subplot(3,1,3)
plt.contourf(palau_dates[79::], p, w*3600, np.linspace(-20, 20, 15), cmap='RdBu_r', extend='both')
plt.gca().invert_yaxis()
plt.colorbar(format='%.0e')
plt.title('Pressure Vel (hPa/hr)')
plt.tight_layout()
plt.show()


In [18]:
rad_frac = np.load('../radar_coverage_fraction.npy')
rad_dates = np.load('../dates.npy', encoding='bytes')

st_date = datetime.datetime(2018,8,22)
end_date = datetime.datetime(2018,9,2)

plt.close('all')

plt.figure()
plt.subplot(2,1,1)
plt.contourf(palau_dates[79::], p, w*3600, np.linspace(-20, 20, 15), cmap='RdBu_r', extend='both')
plt.gca().invert_yaxis()
#plt.colorbar(format='%.0e')
plt.title('Pressure Vel (hPa/hr)')
plt.xlim([st_date, end_date])

plt.subplot(2,1,2)
plt.plot(rad_dates, rad_frac)
plt.xlim([st_date, end_date])

plt.tight_layout()
plt.show()

In [19]:
rad_ordd = np.asarray([rad_dates[i].timestamp() for i in range(len(rad_dates))])
#pal_u_int = pal_u[:, 79::]

#tom_v_int = np.empty(tom_u_int.shape)
#yap_v_int = np.empty(yap_u_int.shape)
#pal_v_int = pal_v[:, 79::]

rad_frac_int = np.interp(pal_ordd[79::], rad_ordd, rad_frac)


In [20]:
w850 = w[np.argmin(abs(p - 850)), :]

In [21]:
plt.close('all')
plt.figure()
plt.plot(palau_dates[79::], (w850-w850.mean())/w850.std(), label='velocity' )
plt.plot(palau_dates[79::], (rad_frac_int - rad_frac_int.mean())/rad_frac_int.std(), label='rain_frac')
plt.legend()
plt.show()

In [22]:
np.cov(w850, rad_frac_int)

array([[  1.26949735e-06,   9.97533104e-07],
       [  9.97533104e-07,   3.06092297e-03]])

In [23]:
np.cov?